In [ ]:
"""
This notebook is used to find the overlap between te AIBL database and NIO dictionary.

"""

In [52]:
import pandas as pd
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)
import xmltodict
from IPython.core.display import HTML


In [3]:
## step1: import all the AIBL concepts 
aibl_path = "/Users/yidesdo21/Projects/inputs/database/aibl_release_notes/aibl-ids-9.0.0-dictionary-202109210351.txt"
aibl_df = pd.read_csv(aibl_path, sep='\t', engine="python")
names = aibl_df["Name"].unique()
names_df = pd.DataFrame(names, columns=["Name"])

In [12]:
part_names = list()
for i in range(1,7):
    part_name = names_df["Name"+str(i)].dropna().unique()
    part_names.append(part_name)
    print("Part"+str(i)+" of the Name has "+str(len(part_name))+" unique terms.")
    print(part_name)
    print("-----------")

Part1 of the Name has 27 unique terms.
['AIBL Id' 'Collection' 'Enrolment' 'Actigraph' 'CSF' 'Demographic' 'Dexa'
 'Image' 'ShortIq' 'Medical History' 'Metals' 'Neuropsych' 'NPIQ'
 'Nutrients from Alcoholic Beverages' 'Nutrients from Food'
 'Nutrients from Food Intakes' 'Nutrients from Raw Data'
 'Blood Processing' 'Pathology' 'Physical Activity' 'Plasma'
 'Progress Summary' 'RBM' 'pha-2 Macroglobulin' 'Vital Signs' 'ADLI'
 'MERCK']
-----------
Part2 of the Name has 1098 unique terms.
['Light' 'Medium' 'Hard' 'Very Hard' 'Avg Counts' 'Peak Counts'
 'TC Daily (x 10^4)' 'K/Cal Daily' 'Timepoint' 'Date of CSF' 'Abeta42'
 'Tau' 'pTau181' 'Elecsys' 'Sex' 'YearMonthOfBirth' 'Site' 'Testing Venue'
 'Current Marital Status' 'Primary Occupation' 'Prim Occ Details'
 'Retirement Status' 'Country of Birth' 'Changes to Living Arrangements'
 'Changed Living Arrang Details' 'Present Living Arrangements'
 'Pres Living Arrang Details' 'Handedness' 'Primary Language at Home'
 'Prim Lang Details' 'Years 

In [13]:
## step2: import all the NIO concepts 
nio_path = "/Users/yidesdo21/Projects/inputs/dictionary/nio_ado.xml"

with open(nio_path) as f:
    nio_xml = f.read()

token_cano = dict()  # {"token_id": "canonical"}
nio_parsed = xmltodict.parse(nio_xml)

In [14]:
nio_dict = nio_parsed["synonym"]["token"]
print("number of token ids:", len(nio_dict)) # number of token ids 

number of token ids: 4847


In [15]:
all_variants = list()
for pair in nio_dict:
    variants = pair["variant"]
    if type(variants) is list:
        for variant in variants:
            var = variant["@base"]
            all_variants.append(var)
    else:
        var = variants["@base"]
        all_variants.append(var)

## avoid cases like "_amyloid beta 42", " attenuation reflex"
nio_concepts = set([x.replace("_", " ").lstrip() for x in all_variants])

In [17]:
## step3: find the intersections between AIBL and NIO
## step 3.1: find the intersections between different name parts of AIBL and NIO 
for i in range(1,7):
    part_name = names_df["Name"+str(i)].dropna().unique()
    print("Part"+str(i)+" of the Name has "+str(len(part_name))+" unique terms.")
    intersection = list(set([x.lower() for x in part_names[i-1]]) & nio_concepts)
    print(str(len(intersection))+" concepts intersect with the NIO dictionary.")
    print(intersection)
    print("-----------")

Part1 of the Name has 27 unique terms.
3 concepts intersect with the NIO dictionary.
['csf', 'image', 'physical activity']
-----------
Part2 of the Name has 1098 unique terms.
56 concepts intersect with the NIO dictionary.
['apoe genotype', 's100b', 'tau', 'diabetes', 'pet', 'site', 'alcohol', 'smoking', 'vcam-1', 'ins', 'stroke', 'c3', 'sex', 'apo-e', 'il-18', 'date', 'iron', 'niacin', 'hypertension', 'folate', 'hcy', 'gro-alpha', 'complement factor h', 'agitation', 'cholesterol', 'calcium', 'esr', 'm-csf', 'fibrinogen', 'gds', 'handedness', 'depression', 'il-6', 'pai-1', 'icam-1', 'apathy', 'ldl', 'il-4', 'il-10', 'vegf', 'eotaxin-3', 'cvlt', 'fe', 'abeta42', 'egf', 'anxiety', 'body mass index', 'trail-r3', 'mif', 'protein', 'il-16', 'il-3', 'cdr', 'g-csf', 'il-8', 'mmse']
-----------
Part3 of the Name has 94 unique terms.
10 concepts intersect with the NIO dictionary.
['hippocampus', 'tau', 'site', 'day', 'repetition', 'memory', 'amyloid', 'year', 'month', 'date']
-----------
Part4 

In [18]:
## step 3.2: find the intersections between the whole name of AIBL and NIO
whole_name = names_df["Name"].unique()
print("Num. of whole name of AIBL concepts:", len(whole_name))
whole_names = set([x.lower().replace(".", " ") for x in whole_name])
intersect_whole_name = list(whole_names & nio_concepts)
print(str(len(intersect_whole_name))+" concepts intersect with the NIO dictionary.")

Num. of whole name of AIBL concepts: 1323
0 concepts intersect with the NIO dictionary.


In [19]:
## step4: examine AIBL
## group the AIBL fields
def examine_group(name):
    """input the name of the field category, i.e., the word before the first dot in each field
    return the field names of that field"""
    print(names_df.loc[names_df['Name1'] == name].iloc[:, 0:2])
    print(names_df.loc[names_df['Name1'] == name].iloc[:, 0:2]["Name"].unique())

In [20]:
names_df["Name1"].dropna().unique()

array(['AIBL Id', 'Collection', 'Enrolment', 'Actigraph', 'CSF',
       'Demographic', 'Dexa', 'Image', 'ShortIq', 'Medical History',
       'Metals', 'Neuropsych', 'NPIQ',
       'Nutrients from Alcoholic Beverages', 'Nutrients from Food',
       'Nutrients from Food Intakes', 'Nutrients from Raw Data',
       'Blood Processing', 'Pathology', 'Physical Activity', 'Plasma',
       'Progress Summary', 'RBM', 'pha-2 Macroglobulin', 'Vital Signs',
       'ADLI', 'MERCK'], dtype=object)

In [21]:
examine_group("Pathology")

                           Name      Name1
989     Pathology.Collection No  Pathology
990   Pathology.Collection Date  Pathology
991              Pathology.Site  Pathology
992                Pathology.Hb  Pathology
993               Pathology.RCC  Pathology
...                         ...        ...
1049               Pathology.Mg  Pathology
1050             Pathology.Fast  Pathology
1051        Pathology.Anion Gap  Pathology
1052           Pathology.Retics  Pathology
1053     Pathology.ReticPercent  Pathology

[65 rows x 2 columns]
['Pathology.Collection No' 'Pathology.Collection Date' 'Pathology.Site'
 'Pathology.Hb' 'Pathology.RCC' 'Pathology.MCV' 'Pathology.MCH'
 'Pathology.MCHC' 'Pathology.RDW' 'Pathology.ESR' 'Pathology.Plt'
 'Pathology.MPV' 'Pathology.WCC' 'Pathology.Neut' 'Pathology.Lymp'
 'Pathology.Mono' 'Pathology.Eos' 'Pathology.Baso' 'Pathology.HCY'
 'Pathology.B12' 'Pathology.sFol' 'Pathology.rFol' 'Pathology.Na'
 'Pathology.K' 'Pathology.HCO3' 'Pathology.Urea' 'Pathology

In [52]:
examine_group("Nutrients from Raw Data")

                                      Name                    Name1
869        Nutrients from Raw Data.Barcode  Nutrients from Raw Data
870           Nutrients from Raw Data.Date  Nutrients from Raw Data
871        Nutrients from Raw Data.Scan no  Nutrients from Raw Data
872      Nutrients from Raw Data.Fruit p d  Nutrients from Raw Data
873        Nutrients from Raw Data.Veg p d  Nutrients from Raw Data
..                                     ...                      ...
983     Nutrients from Raw Data.White wine  Nutrients from Raw Data
984    Nutrients from Raw Data.Port/sherry  Nutrients from Raw Data
985        Nutrients from Raw Data.Spirits  Nutrients from Raw Data
986      Nutrients from Raw Data.Glass p d  Nutrients from Raw Data
987  Nutrients from Raw Data.Max glass p d  Nutrients from Raw Data

[119 rows x 2 columns]
['Nutrients from Raw Data.Barcode' 'Nutrients from Raw Data.Date'
 'Nutrients from Raw Data.Scan no' 'Nutrients from Raw Data.Fruit p d'
 'Nutrients from Raw Da

In [37]:
# examine the descriptions of the fields
descri_df = aibl_df[['Name','Description']]
descri_df = descri_df.join(descri_df['Name'].str.split('.', expand=True).add_prefix('Name'))
pathology = descri_df.loc[descri_df['Name0'] == "Pathology"][["Name1","Description"]]

In [55]:
display(HTML(pathology.to_html()))

In [60]:
# overlap between pathology fields and gene ptc
ptc_path = "/Users/yidesdo21/Projects/inputs/database/ptc/"

with open(ptc_path+'gene2pubtatorcentral', 'rb') as f:
    gene_content = f.readlines()

In [61]:
mentions = set()

for content in gene_content:
    str_content = content.decode().split("\t")
    mention = str_content[3]
    mentions.add(mention)

In [89]:
mention_phrases = list()
for mention in list(mentions):
    ms = [m.lower() for m in mention.split("|")]
    mention_phrases.extend(ms)


In [101]:
for ms in list(ms_set):
#     print(ms.split())
    for patho in list(patho_set):
        if patho in ms.split():
            print(patho,"|",ms)
            print("--------------")
    

= | beta8 = beta14, beta3 = beta9
--------------
of | signal transducers and activators of transcription-1
--------------
8 | cxcl1, 2, 3, 5, 6 or 8
--------------
protein | ldl-receptor-associated protein
--------------
transferase | alanineamino transferase
--------------
protein | fibroblast growth factor receptor 4, aryl hydrocarbon receptor-interacting protein
--------------
specific | prostate specific module
--------------
prostate | prostate specific module
--------------
protein | gs homeobox protein 1
--------------
= | mu1e(k - 1) mu, thetak = theta1e(k - 1
--------------
- | mu1e(k - 1) mu, thetak = theta1e(k - 1
--------------
protein | np, nucleoprotein gene; pa, polymerase acidic, pb1, basic polymerase protein 1
--------------
mean | mtr phalloidin mean +- sd (mum) 1
--------------
protein | tumour necrosis factor, alpha-induced protein 3
--------------
- | beta11 (aopen)  - 1.171 beta12 (slaopen)  - 9
--------------
of | heat shock-cognate chaperone of 70kda
-----------

cell | b cell lymphoma 2 like 1
--------------
protein | protein arginine-methyltransferase-1
--------------
aspartate | glutamate/ aspartate transporter
--------------
of | area product of 1 omega (mum) 2
--------------
= | n = 4) fa (n = 4
--------------
protein | nod-, lrr-, and pyrin domain-containing protein (nlrp) 3
--------------
phosphatase | protein tyrosine phosphatase non-receptor type-22
--------------
protein | protein tyrosine phosphatase non-receptor type-22
--------------
- | n - 1)/2, t) - 1
--------------
free | specific pathogen free (spf) grade apolipoprotein (apo)e
--------------
specific | specific pathogen free (spf) grade apolipoprotein (apo)e
--------------
vitamin | vitamin a, vitamin b1, b2 and b6
--------------
8 | transient receptor potential cation channel, subfamily m, member 8
--------------
+ | naa/total creatine + phosphocreatine (tcr)
--------------
to | related to ubiquitin-1
--------------
of | suppressor of ty 7-like
--------------
- | inf (a - 121

protein | heat shock protein 86
--------------
- | alpha2 - macroglobulin
--------------
protein | link protein
--------------
8 | age, yr 52 +- 14   m 8 (42)   bmi
--------------
= | xp = 1 or 2
--------------
- | median (iqr) 2 (0 - 3) 2 (1 - 4) 1 (0 - 3
--------------
of | cytoplasmic level of inhibitors of kappabalpha (ikappabalpha)
--------------
level | cytoplasmic level of inhibitors of kappabalpha (ikappabalpha)
--------------
of | aminopeptidase regulator of tnfr1 shedding
--------------
8 | erk                             8
--------------
- | ctx-m-15 1 st412 - - 1 st485 - - 2 st628 cro
--------------
protein | t-complex protein component-8
--------------
to | v1 (type 8) to th
--------------
8 | hepatocyte-type cytokeratins (cytokeratin 8 and 18
--------------
total | zagreb 1/4 1/5 2/9     total 24
--------------
of | suppressor of cytokine signaling 1"
--------------
= | edss = 2
--------------
of | signal transducing activators of transcription (stat) 1 and 2
------------

= | h1/2 = h
--------------
lipoprotein | low-density lipoprotein receptor related protein-1
--------------
= | nacc = 1
--------------
= | l 1 (l 1 = l 2
--------------
glucose | insulin-dependent glucose transporter- (glut-) 4
--------------
= | bone morphogenetic protein = 2
--------------
protein | bone morphogenetic protein = 2
--------------
- | macrophage - colony stimulating factor
--------------
stimulating | macrophage - colony stimulating factor
--------------
16 | or 16
--------------
8 | q6, 7, and 8
--------------
phosphatase | collagen alpha-1(i) chain, and alkaline phosphatase
--------------
alkaline | collagen alpha-1(i) chain, and alkaline phosphatase
--------------
binding | atp/gtp binding protein 1
--------------
protein | atp/gtp binding protein 1
--------------
protein | cold shock domain protein 2
--------------
+ | t1/2 120 + 30
--------------
phosphatase | protein phosphatase type-1 (pp1)
--------------
protein | protein phosphatase type-1 (pp1)
--------------

insulin | insulin receptor substrate-1"
--------------
of | lane 1 of fig. 1
--------------
aminotransferase | aspartate aminotransferase (450 iu/l), alanine aminotransferase
--------------
alanine | aspartate aminotransferase (450 iu/l), alanine aminotransferase
--------------
aspartate | aspartate aminotransferase (450 iu/l), alanine aminotransferase
--------------
protein | ring finger protein 18
--------------
specific | p 1 and der p 1 specific igg and ige
--------------
protein | tafa4 protein
--------------
protein | vesicle-soluble n-ethylmaleimide-sensitive factor attachment protein receptor
--------------
hormone | 'gonadotropin-releasing hormone
--------------
= | muc = 9
--------------
of | shz domain-containing leukocyte protein of 76 kda
--------------
protein | shz domain-containing leukocyte protein of 76 kda
--------------
of | c1'/c6/c8 of hp-gt
--------------
protein | yes-associated protein
--------------
= | med = 3
--------------
protein | nap1-related protein 2
-

...

--------------
- | tt(419) tt(270) t 1 - 1   tc(424) tc(361) c 0.74
--------------
8 | caspase 8
--------------
antigen | endothelial barrier antigen (eba) (magenta) and occludin
--------------
cell | cd4-, cd8- t cell receptor-gamma
--------------
protein | trap1-like protein
--------------
protein | 60s ribosomal protein l37
--------------
of | m of 
--------------
+ | + langerin+
--------------
protein | starch-binding protein domain 1
--------------
antigen | type i lewis antigen (leb)
--------------
to | xbp-1 to gapdh
--------------
- | pog - nb/a
--------------
= | gamma = b2
--------------
of | tissue inhibitor of metalloproteinases (timp)-1, -2 and -4
--------------
protein | dystroglycan and protein o-mannosyltransferases 1 and 2
--------------
protein | cdkn1a(p21)-interacting protein
--------------
= | or = 3.7
--------------
protein | apoptosis-stimulating p53-binding protein 2
--------------
- | peg - 10
--------------
protein | high-mobility-group protein hmgi-c
--------

--------------
protein | wnt-inducible signaling protein 2
--------------
the | sperm protein associated with the nucleus on the x chromosome c
--------------
protein | sperm protein associated with the nucleus on the x chromosome c
--------------
gamma-glutamyl | pyruvic transaminase, glutamic oxaloacetic transaminase, gamma-glutamyl transpeptidase
--------------
cell | t cell transcription factor
--------------
+ | jnk (mean +
--------------
protein | gtpase-activating protein (sh3 domain)-binding protein 2
--------------
protein | nijmegen breakage syndrome protein
--------------
protein | centromere-associated protein v
--------------
protein | bilin-binding protein 1
--------------
phosphatase | sh2 domain-containing protein phosphatase 1
--------------
protein | sh2 domain-containing protein phosphatase 1
--------------
protein | rb-e2f-associated apoptotic response. one protein tyrosine phosphatase, ptp-1b
--------------
= | t1/2 = 175
--------------
protein | neural salient ser

8 | tspan 8
--------------
phosphatase | wild-type p53-induced phosphatase (wip)-1
--------------
hormone | anti-thyrotropin-releasing hormone
--------------
phosphatase | cdc25b phosphatase
--------------
protein | tumor necrosis factor (tnf)-stimulated protein 6
--------------
cell | t cell receptor beta chain
--------------
cell | cell intracellular antigen-1 and granzyme b
--------------
protein | cysteine-rich protein 3
--------------
albumin | c-reactive protein to albumin (crp/alb
--------------
to | c-reactive protein to albumin (crp/alb
--------------
protein | c-reactive protein to albumin (crp/alb
--------------
protein | c1q complement/tnf-related protein (ctrp) 1
--------------
- | s[p1 - 1
--------------
- | a - 20 khz, b - 40 khz, and c - 60
--------------
protein | tlr domain-containing adaptor protein inducing interferon-b
--------------
of | dumbfounded/kin of irre (duf/kirre)
--------------
volume | name volume (ml) cu(py)4(otf)2
--------------
- | cd + 6 60 min 3 - 

- | cpg (2 - 4
--------------
protein | homeobox protein 2
--------------
protein | carnitine palmitoyltransferase 1a, angiopoietin-like 4 protein
--------------
= | zk = 1
--------------
protein | ras-gtpase activating protein
--------------
of | b2 (concatenation of (8) + (9)-(4)
--------------
+ | b2 (concatenation of (8) + (9)-(4)
--------------
of | signal transducer and activator of transcription)3
--------------
8 | chx (10 mug/ml) for 4 and 8 h
--------------
protein | nerve growth factor-induced protein i-b
--------------
calcium | serum paraoxonase/arylesterase 1 and tumor-associated calcium signal transducer 2
--------------
serum | serum paraoxonase/arylesterase 1 and tumor-associated calcium signal transducer 2
--------------
8 | mpp 8
--------------
lipoprotein | pemt-/-/low density lipoprotein receptor
--------------
density | pemt-/-/low density lipoprotein receptor
--------------
of | tumor necrosis factor-like weak inducer of apoptosis (tweak)
--------------
protein |

KeyboardInterrupt: 